<h2 style="text-align: center;">How to reduce RGS data and extract spectra and lightcurves of point-like sources</h2>
<br>
<center>
<table border="0" style="background-color: #DDDDDD; width: 100%;">
	<tbody>
		<tr>
			<td style="padding: 2px; text-align: left;">
			<p><b>Introduction</b></p>
			<p style="text-align: justify;">This thread contains a step-by-step recipe to process RGS data of point-like sources.</p>
            <p style="text-align: justify;">The purpose of this jupyter notebook thread is to illustrate how to use SAS within python notebooks. For an in-depth explanation on how to reduce RGS data using SAS, please refer to the standard SAS threads,</p>
                <ul>
                <li><a href="https://www.cosmos.esa.int/web/xmm-newton/sas-thread-rgs">How to reduce RGS data and extract spectra of point-like sources</a></li>
                </ul>
			<p><b>Expected Outcome</b></p>
			<p style="text-align: justify;">Source and background RGS spectra and the associated response matrices as well as lightcurves.</p>
			<p><b>SAS Tasks to be Used</b></p>
			<ul>        
				<li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/rgsproc/index.html" target="_parent"><tt>rgsproc</tt></a></li>
				<li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/rgsfilter/index.html" target="_parent"><tt>rgsfilter</tt></a></li>
                <li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/rgsimplot/index.html" target="_parent"><tt>rgsimplot</tt></a></li>
                <li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/evselect/index.html" target="_parent"><tt>evselect</tt></a></li>
				<li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/tabgtigen/index.html" target="_parent"><tt>tabgtigen</tt></a></li>
			</ul>
			<p><b>Prerequisites</b></p>
			<ul>
				<li><a href="https://www.cosmos.esa.int/web/xmm-newton/sas-thread-startup" target="_parent">SAS Startup Thread</a></li>
			</ul>
			<p><b>Useful Links</b></p>
			<ul>
                <li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/pysas/index.html"><tt>pysas</tt></a></li>
                <li><a href="https://www.cosmos.esa.int/web/xmm-newton/sas-thread-startup-in-python">SAS Startup Thread in Python</a></li>
				<li><a href="https://xmm-tools.cosmos.esa.int/external/xmm_user_support/documentation/sas_usg/USG/rgsanalysis.html">SAS Users Guide: Analysis of RGS data</a></li>
                <li><a href="https://xmm-tools.cosmos.esa.int/external/xmm_user_support/documentation/uhb/rgs.html">XMM-Newton Users Handbook: The Reflection Grating Spectrometers</a></li>
                <li><a href="https://www.cosmos.esa.int/documents/332006/538342/Charo_RGS_Point_Sources_14.pdf">RGS Data Reduction and Analysis of Point-like Sources</a></li>
			</ul>
			<p><b><a href="#cav">Caveats</a></b></p>
			<h4>Last Reviewed: <i>25 May 2023, for <tt>SAS v21.0</tt></i></h4>
			<h4>Last Updated: <i>25 May 2023</i></h4>
			</td>
		</tr>
	</tbody>
</table>
</center>

<hr />
<h2>Procedure</h2>
<p style="text-align: justify;">This thread is intended to show the steps to follow to extract RGS spectra and lightcurves from a Jupiter notebook. It expects that the ODF or PPS have been downloaded into separate folders and that the SAS Startup Thread has been followed.</p>

<p style="text-align: justify;">The task <i>rgsproc</i> can redo different stages of processing without starting from scratch. Allow enough time for it to finish. It may take between 5-10 minutes depending on the ODF size and your computer. The different entry and exit points are called processing stages, of which there are six:</p>
<ul>
    <li>1:events	preliminary tasks, source-independent calibrations
    <li>2:angles	aspect-drift corrections
    <li>3:filter	filters events and exposure
    <li>4:spectra	generates spectra
    <li>5:fluxing	generates response matrices and a combined flux-calibrated spectrum
    <li>6:lightcurve	generates lightcurves
</ul>   

<p style="text-align: justify;">If the task has been run only through spectra neither the response matrices nor the fluxed spectra or the lightcurves are created. The fluxing stage is the most time consuming, and therefore it is recommended to run it only once the results of the previous stages are satisfactory.</p>
<hr />

<p style="text-align: justify;"><b>In order to run the following blocks, SAS needs to be inizialized in the terminal from which the Jupyter nootebook has been opened. This has to be done prior to launching the notebook. Follow the steps provided in the <i>SAS Startup Thread in Python</i>.</b></p>

<p style="text-align: justify;">Import the following Python libraries,</p>

In [ ]:
from pysas.wrapper import Wrapper as w
import os, sys,glob,shutil
import pathlib
from astropy.io import fits
from astropy import coordinates as coo
from astropy import units as u
import numpy as np
import matplotlib.pyplot as plt
from astropy.io import fits
from astropy.table import Table
from astropy.convolution import Gaussian2DKernel, convolve

<p style="text-align: justify;">Before we start, lets see what we have already defined in terms of SAS variables,</p>

In [ ]:
inargs = []
t = w('sasver', inargs)
t.run()

<p style="text-align: justify;">We still need to define the <tt>SAS_ODF</tt> and <tt>SAS_CCF</tt> variables (make sure the SAS_CCFPATH is also defined). Use the SAS task <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/startsas/index.html"><tt>startsas</tt></a> as described in the <i>SAS Startup Thread in Python</i> to download an ODF. For this thread, we will assume that an ODF has already been downloaded. We will use the ODF with id <tt>00096020101</tt> as an example and assume that there is already a directory (<tt>sas_file</tt> in the block below) with an existing <tt>CIF</tt> and SAS Summary File. In the block below introduce the absoute path to the <tt>Working directory</tt> (finished with '/') and the location of the <tt>CIF</tt> and SAS Summary File,</p>

<i><u>Note:</u> the path to the <tt>CIF</tt> and SAS Summary File must be an absolute path begining with '/'.</i>

In [ ]:
work_dir = 'absolute_path_to_wrk_directory'
sas_file = 'absolute_path_to_cifSUMSAS_directory'

In [ ]:
inargs = [f'sas_ccf={sas_file}ccf.cif', f'sas_odf={sas_file}0082_0096020101_SCX00000SUM.SAS', f'workdir={work_dir}']

In [ ]:
w('startsas', inargs).run()

<p style="text-align: justify;">This process should have defined the <tt>SAS_CCF</tt> an <tt>SAS_ODF</tt> variables.</p> 

<p style="text-align: justify;">In the following blocks we will produce an RGS event file and associated files to extract a spectra and lightcurves of point-like source.</p>

<ul>
    <li style="text-align: justify;">First, run the <i>rgsproc</i> task with no further parameters. The default entry and final stages are <b>1:events</b> and <b>6:lightcurve</b>, respectively.</li>
</ul>

In [ ]:
# SAS Command
cmd        = "rgsproc" # SAS task to be executed                  

# Arguments of SAS Command
inargs = [ ]           # do not provide any parameters 

# Execute the SAS task to obtain RGS products
w(cmd, inargs).run()

<p style="text-align: justify;">For most analysis, this is all is needed, however, there are a number of checks we can do.</p> 

<h3>Checking for periods of high background activity</h3>

<p style="text-align: justify;">In line with the other XMM-Newton instruments, RGS observations can be affected by high particle background periods caused by solar activity or by the Earth radiation belts. You should check your observations and, if necessary, filter out these periods before extracting any scientific products. In the blocks that follow will we use RGS1. The equivalent commands can be used for RGS2. We will use the ODF with id <tt>0096020101</tt> as an example.</p>
<ul>
    <li style="text-align: justify;">Create a light curve of the pure background events. For this, only events in the background region of CCD number 9 are selected as it is the one closest to the optical axis of the telescope, and the most affected by background flares. </li>
</ul>

In [ ]:
# Define some RGS1 files needed in the next blocks

evt_list     = work_dir+'P0096020101R1S004EVENLI0000.FIT'  # event list
src_list     = work_dir+'P0096020101R1S004SRCLI_0000.FIT'  # source list
mer_list     = work_dir+'P0096020101R1S004merged0000.FIT'  # combined event list

In [ ]:
# Function to plot Lightcurve
def plotLC(plt,threshold,fileName):        
        if fileName != "NOT FOUND":
            fitsFile = fits.open(fileName)   
            prihdu   = fitsFile[1].header
            if ('CUTVAL' in prihdu):
                threshold = prihdu['CUTVAL']

            cols    = fitsFile[1].columns
            colName = None
            for i,x  in enumerate(cols.names):
                if "RATE" in x:
                    colName = cols.names[i]
                if "COUNTS" in x:
                    colName = cols.names[i]        

            data = fitsFile[1].data   
            
            xdata = data.field('TIME') - min(data.field('TIME')) # extract the x data column
            ydata = data.field(colName)

            xmax=np.amax(xdata) 
            xmin=np.amin(xdata) 

            plt.plot(xdata,ydata,label=fileName) # plot the data

            if colName == 'RATE':
                plt.title("Lightcurve")
                plt.xlabel("Time (s)")
                plt.ylabel("Cts/s")
            else:
                plt.title("Lightcurve")
                plt.xlabel("Time (s)")
                plt.ylabel("Counts")

            if (threshold != 'None'):
                if (colName == 'COUNTS'):
                    threshold=float(threshold)*100.

                y2data = [threshold]*len(xdata)            
                plt.plot(xdata,y2data)
                plt.text(xmin+0.1*(xmax-xmin), threshold+0.01*threshold, str(threshold)+" cts/sec", ha='center')        
 
            fitsFile.close()   
            
        else:
            print("File not found "+fileName+"\n")

In [ ]:
# Function to plot RGS plots
def plotRGS(plt,fileName,rgsfile,srcfile,source): 
    hdu=fits.open(fileName)
    hdr=hdu[1].header
    ev=Table(hdu[1].data)

    plt.subplot(2,1,1)
    
    img=plt.hist2d(ev['M_LAMBDA'],ev['PI'],[360,250],cmap='Oranges',vmin=0,vmax=5)
    hdu.close()
    
    hdu=fits.open(srcfile)
    inst=hdr['INSTRUME'].strip()
    reg=Table(hdu[inst+'_SRC'+str(source)+'_ORDER_1'].data)
    nreg=len(reg)
    
    for i in range(nreg):
        rr=reg[i]
        ii=np.nonzero(rr['LAMBDA'])
        if rr['SHAPE'][0] == '!':
            linest=':r'
        else:
            linest='-b'
        plt.plot(rr['LAMBDA'][ii],rr['PI'][ii],linest)
        
    plt.title(os.path.basename(fileName))
    plt.xlabel('Wavelength (A)')
    plt.ylabel('PI (eV)')
 
    hdu.close()
    
    plt.subplot(2,1,2)

    hdus=fits.open(rgsfile)
    r1=Table(hdus[1].data)
    xdsp=np.degrees(r1['XDSP_CORR'])*3600.
    plt.rcParams["figure.figsize"]=(12,6)
    img,xe,ye=np.histogram2d(xdsp,r1['M_LAMBDA'],[250,250]) 

    kernel=np.array([[1,1,1],[1.,3.,1.],[1.,9,1.],[1.,3.,1.],[1.,1,1.]])
    kernel=kernel/np.sum(kernel)
    imgs=convolve(img,kernel)

    plt.imshow(imgs,origin='lower',vmin=0,vmax=1.5,cmap='rainbow',
          extent=[ye[0],ye[-1],xe[0],xe[-1]],aspect='auto',)

    hdus.close()
    
    hdul=fits.open(srcfile)
    src=Table(hdul['SRCLIST'].data)
    dd=src['DELTA_XDSP']*(-60)    
    reg=Table(hdul['RGS1_SRC'+str(source)+'_SPATIAL'].data)
    nreg=len(reg)

    for i in range(nreg):
        rr=reg[i]
        ii=np.nonzero(rr['LAMBDA'])
        plt.plot(rr['LAMBDA'][ii],np.degrees(rr['XDSP_CORR'][ii])*3600,'r')
    reg=Table(hdul['RGS1_BACKGROUND'].data)
    nreg=len(reg)
    
    for i in range(nreg):
        rr=reg[i]
        ii=np.nonzero(rr['LAMBDA'])
        if rr['SHAPE'][0] != '!':
            linest='-g'
        else:
            linest='--y' 
        plt.plot(rr['LAMBDA'][ii],np.degrees(rr['XDSP_CORR'][ii])*3600,linest,clip_on=True)
 
    plt.xlabel('Wavelength')
    plt.ylabel('Cross-dispersion (arcsec)')
    plt.xlim([6.,32.])

    hdul.close()

In [ ]:
# Define a SAS filter expression to derive a background rate cut

lc_binsize   = 100      # lightcurve bin size in secs

out_LCFile   = work_dir+'RGS1_FlareBKGRate.fit'  # Name of the output BKG lightcurve

In [ ]:
# SAS Command
cmd        = "evselect" # SAS task to be executed                  

# Arguments of SAS Command
expression = f'(CCDNR==9)&&(REGION({src_list}:RGS1_BACKGROUND,M_LAMBDA,XDSP_CORR))'  # event filter expression
inargs     = [f'table={evt_list}','withrateset=Y',f'rateset={out_LCFile}','maketimecolumn=Y',f'timebinsize={lc_binsize}','makeratecolumn=Y',f'expression={expression}']      

print("   Filter expression to use: "+expression+" \n")
print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
# Execute the SAS task with the parameters to produce the flaring background lightcurve.

w(cmd, inargs).run()

<ul>
    <li style="text-align: justify;">Check the created background light curve.</li>
</ul>

In [ ]:
# Inspect light curve

rgs_threshold = 0.1         # Rate cts/sec (only used here for display purposes. Draws a horizontal line at this value)
plt.figure(figsize=(20,8))  # Size of figure

plotLC(plt,rgs_threshold,out_LCFile) # Plot source region light curve

plt.legend()

<ul>
    <li style="text-align: justify;">If necessary, create an additional GTI for filtering periods of high background out of the event list, to be used in conjunction with the internal GTI tables. The expression in the <tt>tabgtigen</tt> task indicates that only periods with count rates less than <tt>rgs_rcut</tt> counts/sec should be selected. The value of <tt>rgs_rcut</tt> should be chosen after inspection of the background light curve; it goes typically from 0.1 to 2 counts/sec.</li>
</ul>

In [ ]:
# Define some parameters to produce the gti file

rgs_rcut    = 0.1     # Rate cts/sec 

gti_list    = work_dir+'RGS1_GTI.fit'  # Name of the output GTI file 

In [ ]:
# SAS Command
cmd        = "tabgtigen" # SAS task to be executed                  

# Arguments of SAS Command
expression = f'(RATE<{rgs_rcut})'
inargs     = [f'table={out_LCFile}',f'gtiset={gti_list}',f'expression={expression}']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs  

In [ ]:
# Execute the SAS task with the parameters to produce GTI file

w(cmd, inargs).run()

<ul>
    <li style="text-align: justify;">Re-process the data with <tt>rgsfilter</tt>. The filter stage requires a combined event list named <tt>PxxxxxxyyyyRrzeeemerged0000.FIT</tt> as input. Since we have already run <tt>rgsproc</tt> already, such a file has been created and it is in the working directory.</li>
</ul>

In [ ]:
# SAS Command
cmd        = "rgsfilter" # SAS task to be executed                  

# Arguments of SAS Command
inargs     = [f'mergedset={mer_list}',f'evlist={evt_list}',f'auxgtitables={gti_list}']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs   

In [ ]:
# Execute the SAS task with the parameters to filter RGS file

w(cmd, inargs).run()

<ul>
    <li style="text-align: justify;">Run <tt>rgsproc</tt> from the <b>spectra</b> stage to obtain the spectral products after GTI filtering.</li>    
</ul>

In [ ]:
# SAS Command
cmd        = "rgsproc" # SAS task to be executed                  

# Arguments of SAS Command
inargs     = [f'auxgtitables={gti_list}',f'entrystage=\'4:spectra\'']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs  

In [ ]:
# Execute the SAS task with the parameters to produce RGS spectral products after gti filtering

w(cmd, inargs).run()

<ul>
    <li style="text-align: justify;">Display the dispersion vs cross dispersion and dispersion vs energy images and overlay the selected region masks.</li>
</ul>

In [ ]:
# Define some parameters for evselect

outfile   ='RGS1.fits' # Output event file name

In [ ]:
# SAS Command
cmd        = "evselect" # SAS task to be executed                  

# Arguments of SAS Command
expression = f'REGION({src_list}:RGS1_SRC1_ORDER_1,M_LAMBDA,PI)'
inargs=[f'table={evt_list}',f'expression={expression}',f'keepfilteroutput=yes',f'withfilteredset=yes',f'filteredset={outfile}']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs                                    

In [ ]:
# Execute the SAS task with the parameters to produce an image

w(cmd, inargs).run()

In [ ]:
# Inspect plots

plt.figure(figsize=(20,18))  # Size of figure

source = 1 # if user has defined the coordinate (1: default ; 3: user defined)
plotRGS(plt,evt_list,outfile,src_list,source) # Plot RGS plots

plt.legend()

<ul>
    <li style="text-align: justify;">In the figure above, red solid lines indicate the source spectrum extraction region; yellow dashed lines indicate excluded areas for background spectrum extraction; and the green solid lines correspond to the background spectrum extraction region.</li>
    <li> It is very important to check that the selection regions are correctly centred on the prime source. Also, check that the region used for background extraction excludes other existing sources.
</ul>

<h3> Changing the coordinates of the prime source</h3>

<ul>
    <li style="text-align: justify;">The coordinates of the prime source can be changed (in case for example that they are incorrect). The new coordinates can be entered and added to the source list. Add to the argument list (<tt>inargs</tt>) when calling <tt>rgsproc</tt> the following parameters:

    f'withsrc=yes','srclabel=USER',f'srcra={RA}',f'srcdec={DEC}'
    
where the new coordinates are, 
        
    RA  = 184.6110
    DEC =+29.81267        

<i>withscr=yes</i> is used to define a new prime source by the parameters <i>srclabel</i>, <i>srcra</i> and <i>srcdec</i>. The label is the name that the new source will get in the source list, coordinates are J2000 in decimal degrees.
        
See the thread <a href="https://www.cosmos.esa.int/web/xmm-newton/sas-thread-rgs2">rgsproc, Coordinates and Masks</a> for further explanations.</li>
</ul>

In [ ]:
# Define some parameters for rgsproc

RA  = 184.6110  # source RA
DEC =+29.81267   # source DEC

In [ ]:
# SAS Command
cmd        = "rgsproc" # SAS task to be executed                  

# Arguments of SAS Command
inargs=[f'withsrc=yes','srclabel=USER',f'srcra={RA}',f'srcdec={DEC}']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs  

In [ ]:
# Execute the SAS task to run rgsproc changing the source coordinates

w(cmd, inargs).run()

<ul>
    <li style="text-align: justify;">Display again the dispersion vs cross dispersion and dispersion vs energy images and overlay the selected region masks.</li>
</ul>

In [ ]:
# Define some parameters for evselect

outfile   ='RGS1_User.fits' # Output event file name


<ul>
    <li style="text-align: justify;">In the <tt>expression</tt> defined in the block below, notice the change from, <tt>RGS1_SRC1_ORDER_1</tt> to <tt>RGS1_SRC3_ORDER_1</tt>, which indicates that the coordinates of the source being used are those definde by the user.</li>
</ul>

In [ ]:
# SAS Command
cmd        = "evselect" # SAS task to be executed                  

# Arguments of SAS Command
expression = f'REGION({src_list}:RGS1_SRC3_ORDER_1,M_LAMBDA,PI)'
inargs=[f'table={evt_list}',f'expression={expression}',f'keepfilteroutput=yes',f'withfilteredset=yes',f'filteredset={outfile}']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs 

In [ ]:
# Execute the SAS task with the parameters to produce an image

w(cmd, inargs).run()

In [ ]:
# Inspect plots

plt.figure(figsize=(20,18))  # Size of figure

source = 3 # if user has defined the coordinate (1: default ; 3: user defined)
plotRGS(plt,evt_list,outfile,src_list,source) # Plot RGS plots

plt.legend()

<hr />&nbsp;
<center>
<table border="0" style="background-color: #DDDDDD; width: 100%;">
	<tbody>
		<tr>
			<td style="padding: 2px;">
			<p><a name="cav"></a> <b>Caveats</b><br />
			<br />
			None</p>
			</td>
		</tr>
	</tbody>
</table>
</center>
&nbsp;

<hr />
<p>&nbsp;</p>